In [7]:
import ee
ee.Authenticate(force=True)
ee.Initialize(project='ee-prathama76')

Enter verification code: 4/1AQSTgQHBBZVP8LydwOxbvudee871gjCaDuna5cO7FyIwskbC2L_PvZaKiL0

Successfully saved authorization token.


In [8]:
import ee
import pandas as pd

# Initialize the Earth Engine API
ee.Initialize()

# Define the function to fetch SAR data for a given point
def fetch_sar_data_for_point(lat, lon, crop_name, start_date, end_date):
    # Define the point of interest
    point = ee.Geometry.Point(lon, lat)
    
    # Load the Sentinel-1 ImageCollection
    sentinel1 = ee.ImageCollection("COPERNICUS/S1_GRD") \
        .filterBounds(point) \
        .filterDate(start_date, end_date) \
        .filter(ee.Filter.eq("instrumentMode", "IW")) \
        .filter(ee.Filter.inList("orbitProperties_pass", ["ASCENDING", "DESCENDING"])) \
        .select(["VV", "VH"])
    
    # Log the number of images found for the point
    num_images = sentinel1.size().getInfo()
    print(f"Processing point ({lat}, {lon}) - Crop: {crop_name} - Images found: {num_images}")
    
    if num_images == 0:
        print(f"No data found for point ({lat}, {lon}) within the specified time range.")
        return []
    
    # Extract data for the point
    def extract_values(image):
        # Get the mean value for each band at the point
        value = image.reduceRegion(
            reducer=ee.Reducer.mean(),
            geometry=point,
            scale=10
        )
        
        # Get the orbit pass direction (ascending or descending)
        orbit_pass = image.get("orbitProperties_pass")
        
        return ee.Feature(None, {
            "date": image.date().format("YYYY-MM-dd"),
            "VV": value.get("VV"),
            "VH": value.get("VH"),
            "Orbit": orbit_pass,
            "Crop_Name": crop_name
        })
    
    # Map the extraction function to the ImageCollection
    features = sentinel1.map(extract_values).getInfo()["features"]
    
    # Convert features to a list of dictionaries
    data = []
    for feature in features:
        props = feature["properties"]
        data.append({
            "date": props["date"],
            "VV": props["VV"],
            "VH": props["VH"],
            "Orbit": props["Orbit"],  # Include orbit pass direction
            "Crop_Name": props["Crop_Name"],
            "latitude": lat,
            "longitude": lon
        })
    
    return data

# Read the input CSV file
input_csv = "Karnataka_Datasets/Agrifield.csv"  # Replace with your input file path
df = pd.read_csv(input_csv)

# Define the time range for Sentinel-1 data
start_date = "2021-04-01"
end_date = "2021-10-31"

# Initialize an empty list to store results
all_data = []

# Process each row in the CSV
for index, row in df.iterrows():
    lat = row["Latitude"]
    lon = row["Longitude"]
    crop_name = row["Crop_Name"]
    
    # Fetch SAR data for the point
    try:
        sar_data = fetch_sar_data_for_point(lat, lon, crop_name, start_date, end_date)
        if sar_data:
            all_data.extend(sar_data)
        else:
            print(f"No data returned for point ({lat}, {lon})")
    except Exception as e:
        print(f"Error fetching data for point ({lat}, {lon}): {e}")

# Convert all data to a DataFrame
output_df = pd.DataFrame(all_data)

# Check if the DataFrame is empty
if output_df.empty:
    print("No SAR data was retrieved for the given points and time range.")
else:
    # Save the output to a new CSV file
    output_csv = "Karnataka_Datasets/Agrifield_SAR.csv"  # Replace with your desired output file path
    output_df.to_csv(output_csv, index=False)
    print(f"Data successfully saved to {output_csv}")


Processing point (19.286188981169765, 83.39884788522168) - Crop: No Crop/Fallow - Images found: 18
Processing point (19.28218382824294, 83.40888769570374) - Crop: No Crop/Fallow - Images found: 18
Processing point (19.274077490545768, 83.41135111694561) - Crop: No Crop/Fallow - Images found: 18
Processing point (25.576379322808634, 87.44469489298854) - Crop: No Crop/Fallow - Images found: 53
Processing point (25.58443108803743, 87.44496037785558) - Crop: Maize - Images found: 53
Processing point (25.57874959821723, 87.44691683244083) - Crop: Maize - Images found: 53
Processing point (25.58113095880816, 87.43958604646521) - Crop: Potato - Images found: 53
Processing point (25.580502907101057, 87.43849983973524) - Crop: Potato - Images found: 53
Processing point (25.4156385365353, 76.5238002207973) - Crop: Wheat - Images found: 25
Processing point (25.41395828410415, 76.52440404234842) - Crop: Wheat - Images found: 25
Processing point (27.48601319963976, 82.47641687911434) - Crop: Wheat 

Processing point (27.6462309474625, 82.17384099646662) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.646298419479454, 82.17653518580248) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.64596290164912, 82.17713880065948) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.64537628455708, 82.17750100044321) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.645131062343246, 82.17353678486629) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.64491905307684, 82.17942776666509) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.64458743342521, 82.17988908344867) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.6443025338183, 82.17962270288687) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.64124192176936, 82.17476144687274) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.637171147758487, 82.16786448327511) - Crop: No Crop/Fallow - Images found: 53
Processing point (2

Processing point (24.656034432675348, 76.89987247839125) - Crop: Mustard - Images found: 42
Processing point (27.58440682447113, 81.39683464825765) - Crop: Wheat - Images found: 53
Processing point (27.58312168863517, 81.3895427089092) - Crop: Wheat - Images found: 53
Processing point (27.57335030707789, 81.40127780621933) - Crop: Wheat - Images found: 53
Processing point (27.57137174734545, 81.39880525443225) - Crop: Wheat - Images found: 53
Processing point (27.57118644058443, 81.39530456682954) - Crop: Wheat - Images found: 53
Processing point (27.56757516411569, 81.39505091462894) - Crop: Wheat - Images found: 53
Processing point (27.56724786691598, 81.39377718962005) - Crop: Wheat - Images found: 53
Processing point (27.58700455260593, 81.39069845702882) - Crop: Mustard - Images found: 53
Processing point (27.58324614547648, 81.39810264927176) - Crop: Mustard - Images found: 53
Processing point (27.58231168667588, 81.40213650536317) - Crop: Mustard - Images found: 53
Processing po

Processing point (25.22210341023104, 76.32949425883491) - Crop: Wheat - Images found: 25
Processing point (25.20172503119954, 76.33793015989947) - Crop: Wheat - Images found: 25
Processing point (27.6092199537593, 82.26629789368987) - Crop: Wheat - Images found: 53
Processing point (24.810229560954834, 76.78114623698558) - Crop: Wheat - Images found: 42
Processing point (25.3098230198812, 76.38591369644475) - Crop: Wheat - Images found: 25
Processing point (25.308733597508496, 76.3903621222844) - Crop: Wheat - Images found: 25
Processing point (25.303801786094034, 76.37734090314751) - Crop: Mustard - Images found: 25
Processing point (25.04952283212902, 76.39670543893993) - Crop: Mustard - Images found: 25
Processing point (27.97394355019707, 81.49594379166298) - Crop: Wheat - Images found: 53
Processing point (27.973169435183635, 81.49489549790952) - Crop: Wheat - Images found: 53
Processing point (25.51083545343984, 87.60345891742477) - Crop: Wheat - Images found: 35
Processing point

Processing point (25.38993385036056, 87.7321248396823) - Crop: Maize - Images found: 35
Processing point (24.642751543646654, 76.78139036414888) - Crop: Garlic - Images found: 42
Processing point (25.46123482897323, 87.80067155288421) - Crop: Mustard - Images found: 35
Processing point (25.46001495025904, 87.80032689400308) - Crop: Mustard - Images found: 35
Processing point (25.479379966710464, 87.79170900708695) - Crop: Rice - Images found: 35
Processing point (25.46024011673578, 87.81232330533295) - Crop: Rice - Images found: 35
Processing point (27.75268681607012, 81.53716677010726) - Crop: Wheat - Images found: 53
Processing point (27.75170169605058, 81.53241740429182) - Crop: Wheat - Images found: 53
Processing point (27.75040469811057, 81.53462025099782) - Crop: Wheat - Images found: 53
Processing point (27.75191882536234, 81.53315078083925) - Crop: Lentil - Images found: 53
Processing point (27.75039735130505, 81.5359754887277) - Crop: Lentil - Images found: 53
Processing point

...

Processing point (27.53468072723847, 82.15292817733359) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.53447739503872, 82.15255666914848) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.53426558209158, 82.15317730913466) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.723526453057467, 81.39360401543162) - Crop: Mustard - Images found: 53
Processing point (25.62181185000171, 87.43592178420865) - Crop: Mustard - Images found: 53
Processing point (25.62195922527797, 87.44552385561555) - Crop: Mustard - Images found: 53
Processing point (25.61539261604772, 87.44702244896853) - Crop: Mustard - Images found: 53
Processing point (25.61675077720497, 87.43754717038674) - Crop: No Crop/Fallow - Images found: 53
Processing point (25.615593183033013, 87.44725351195595) - Crop: Maize - Images found: 53
Processing point (25.611574284255106, 87.45815919700019) - Crop: Maize - Images found: 53
Processing point (19.52395855487909, 83.46992912605197) - Crop:

Processing point (27.646865155309506, 82.29764413506838) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.195958473844133, 81.49682558238064) - Crop: Wheat - Images found: 53
Processing point (27.203766870666765, 81.50147854640534) - Crop: Mustard - Images found: 53
Processing point (27.19627437432309, 81.49805266199054) - Crop: Mustard - Images found: 53
Processing point (27.194833743434312, 81.49590272474894) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.19649592692578, 81.49676994491867) - Crop: Green pea - Images found: 53
Processing point (24.81157437482049, 76.63588894697251) - Crop: Wheat - Images found: 42
Processing point (24.81377204684305, 76.6309477105294) - Crop: Mustard - Images found: 42
Processing point (24.81265272332541, 76.63840330801608) - Crop: Mustard - Images found: 42
Processing point (24.80652091854323, 76.63335171332335) - Crop: Mustard - Images found: 42
Processing point (24.80984501812543, 76.63316263461753) - Crop: Garlic - Im

Processing point (27.748882276166, 82.1570281705082) - Crop: Wheat - Images found: 53
Processing point (27.749482659251257, 82.15728725296508) - Crop: Lentil - Images found: 53
Processing point (27.748379438985445, 82.15761534146856) - Crop: No Crop/Fallow - Images found: 53
Processing point (27.580414541706947, 82.27155341147103) - Crop: Lentil - Images found: 53
Processing point (27.56179125066216, 82.28379077306215) - Crop: Lentil - Images found: 53
Processing point (27.573669394773443, 82.28511524877504) - Crop: No Crop/Fallow - Images found: 53
Processing point (25.668135344417426, 87.47057370815892) - Crop: No Crop/Fallow - Images found: 53
Processing point (25.642869867792022, 87.90436192618598) - Crop: Maize - Images found: 35
Processing point (25.64278492708864, 87.90360716082313) - Crop: Maize - Images found: 35
Processing point (27.916976635693448, 81.48793188792399) - Crop: Wheat - Images found: 53
Processing point (27.916691948620983, 81.49408983625474) - Crop: Wheat - Ima

Processing point (27.84964510327372, 81.34756059898173) - Crop: Wheat - Images found: 53
Processing point (27.84911429011566, 81.35600062079895) - Crop: Wheat - Images found: 53
Processing point (27.849035779353954, 81.34466577959004) - Crop: Wheat - Images found: 53
Processing point (27.847917625934084, 81.35352645432458) - Crop: Wheat - Images found: 53
Processing point (27.847733353981244, 81.35225037300685) - Crop: Wheat - Images found: 53
Processing point (27.84633009680983, 81.34699001563622) - Crop: Wheat - Images found: 53
Processing point (27.845997607249, 81.35309969380934) - Crop: Wheat - Images found: 53
Processing point (27.84591122729362, 81.35129702979687) - Crop: Wheat - Images found: 53
Processing point (27.84437607930517, 81.35635630504325) - Crop: Wheat - Images found: 53
Processing point (27.84430988241835, 81.36122556884777) - Crop: Wheat - Images found: 53
Processing point (27.84317015226497, 81.35825597554754) - Crop: Wheat - Images found: 53
Processing point (27

Processing point (19.0862369097799, 83.5400269805388) - Crop: No Crop/Fallow - Images found: 18
Processing point (19.08556298924849, 83.54032663101594) - Crop: No Crop/Fallow - Images found: 18
Processing point (19.085232986268373, 83.54087970543357) - Crop: No Crop/Fallow - Images found: 18
Processing point (19.0835596002816, 83.54039989065495) - Crop: No Crop/Fallow - Images found: 18
Processing point (19.083466524219588, 83.54279778596) - Crop: No Crop/Fallow - Images found: 18
Processing point (24.747577533108664, 76.69466039627375) - Crop: Wheat - Images found: 42
Processing point (24.743962155457915, 76.68932205447292) - Crop: Mustard - Images found: 42
Processing point (27.23462433529524, 81.56936220572851) - Crop: Mustard - Images found: 53
Processing point (27.18961326674866, 82.30275050610857) - Crop: No Crop/Fallow - Images found: 53
Processing point (25.192919242368227, 76.28064571447082) - Crop: Garlic - Images found: 25
Data successfully saved to Karnataka_Datasets/Agrifi

In [ ]:
import os
import ee
import pandas as pd

# Initialize the Earth Engine API
ee.Initialize()

# Define the function to fetch SAR data for a given point
def fetch_sar_data_for_point(lat, lon, crop_name, start_date, end_date):
    # Define the point of interest
    point = ee.Geometry.Point(lon, lat)

    # Load the Sentinel-1 ImageCollection for ascending and descending passes
    sentinel1_asc = ee.ImageCollection("COPERNICUS/S1_GRD") \
        .filterBounds(point) \
        .filterDate(start_date, end_date) \
        .filter(ee.Filter.eq("instrumentMode", "IW")) \
        .filter(ee.Filter.eq("orbitProperties_pass", "ASCENDING")) \
        .select(["VV", "VH"])

    sentinel1_desc = ee.ImageCollection("COPERNICUS/S1_GRD") \
        .filterBounds(point) \
        .filterDate(start_date, end_date) \
        .filter(ee.Filter.eq("instrumentMode", "IW")) \
        .filter(ee.Filter.eq("orbitProperties_pass", "DESCENDING")) \
        .select(["VV", "VH"])

    def extract_values(image, pass_direction):
        # Get the mean value for each band at the point
        value = image.reduceRegion(
            reducer=ee.Reducer.mean(),
            geometry=point,
            scale=10
        )
        return ee.Feature(None, {
            "date": image.date().format("YYYY-MM-dd"),
            "VV": value.get("VV"),
            "VH": value.get("VH"),
            "Crop_Name": crop_name,
            "Pass_Direction": pass_direction
        })

    # Map the extraction function to each ImageCollection
    asc_features = sentinel1_asc.map(lambda img: extract_values(img, "ASCENDING")).getInfo()["features"]
    desc_features = sentinel1_desc.map(lambda img: extract_values(img, "DESCENDING")).getInfo()["features"]

    # Combine features from ascending and descending passes
    data = []
    for feature in asc_features + desc_features:
        props = feature["properties"]
        data.append({
            "date": props["date"],
            "VV": props["VV"],
            "VH": props["VH"],
            "Crop_Name": props["Crop_Name"],
            "Pass_Direction": props["Pass_Direction"],
            "latitude": lat,
            "longitude": lon
        })

    return data

# Define the time range for Sentinel-1 data
start_date = "2021-04-01"
end_date = "2022-03-31"

# Define the input and output directories
input_dir = "Karnataka_Datasets/Across/"  # Replace with your input directory path
output_dir = "Karnataka_Datasets/Across/"  # Replace with your output directory path

# Create the output directory if it doesn't exist
os.makedirs(output_dir, exist_ok=True)

# Process each CSV file in the directory
for file_name in os.listdir(input_dir):
    if file_name.endswith(".csv"):
        input_csv = os.path.join(input_dir, file_name)
        output_csv = os.path.join(output_dir, f"Processed_{file_name}")

        # Log the current file being processed
        print(f"Processing file: {file_name}")

        # Read the input CSV file
        df = pd.read_csv(input_csv)

        # Initialize an empty list to store results
        all_data = []

        # Process each row in the CSV
        for index, row in df.iterrows():
            lat = row["Latitude"]
            lon = row["Longitude"]
            crop_name = row["Crop_Name"]

            # Log the current point being processed
            print(f"Processing point ({lat}, {lon}) - Crop: {crop_name}")

            # Fetch SAR data for the point
            try:
                sar_data = fetch_sar_data_for_point(lat, lon, crop_name, start_date, end_date)
                if sar_data:
                    all_data.extend(sar_data)
                    print(f"Data fetched for point ({lat}, {lon}): {len(sar_data)} records")
                else:
                    print(f"No data returned for point ({lat}, {lon})")
            except Exception as e:
                print(f"Error fetching data for point ({lat}, {lon}): {e}")

        # Convert all data to a DataFrame
        output_df = pd.DataFrame(all_data)

        # Check if the DataFrame is empty
        if output_df.empty:
            print(f"No SAR data was retrieved for file: {file_name}")
        else:
            # Save the output to a new CSV file
            output_df.to_csv(output_csv, index=False)
            print(f"Data successfully saved to {output_csv}")


Processing file: Karnataka_Dataset_Across_Regions.csv
Processing point (12.8073603, 77.7789226) - Crop: Maize
Data fetched for point (12.8073603, 77.7789226): 31 records
Processing point (12.8073629, 77.7788514) - Crop: Maize
Data fetched for point (12.8073629, 77.7788514): 31 records
Processing point (12.7421209, 77.7481075) - Crop: Rose
Data fetched for point (12.7421209, 77.7481075): 31 records
Processing point (12.7421264, 77.7480963) - Crop: Rose
Data fetched for point (12.7421264, 77.7480963): 31 records
Processing point (12.7339533, 77.745245) - Crop: Rose
Data fetched for point (12.7339533, 77.745245): 31 records
Processing point (12.7339673, 77.7452455) - Crop: Rose
Data fetched for point (12.7339673, 77.7452455): 31 records
Processing point (12.7982671, 77.8027552) - Crop: Redgram
Data fetched for point (12.7982671, 77.8027552): 31 records
Processing point (12.7955541, 77.7950533) - Crop: Eucalyptus
Data fetched for point (12.7955541, 77.7950533): 31 records
Processing point 

Data fetched for point (12.7548595, 77.7545334): 31 records
Processing point (12.7548577, 77.7545361) - Crop: Ragi
Data fetched for point (12.7548577, 77.7545361): 31 records
Processing point (12.7627848, 77.7517113) - Crop: Maize
Data fetched for point (12.7627848, 77.7517113): 31 records
Processing point (12.7627968, 77.751695) - Crop: Maize
Data fetched for point (12.7627968, 77.751695): 31 records
Processing point (12.7627876, 77.7516989) - Crop: Maize
Data fetched for point (12.7627876, 77.7516989): 31 records
Processing point (12.7640894, 77.769819) - Crop: Ragi
Data fetched for point (12.7640894, 77.769819): 31 records
Processing point (12.7360151, 77.7601675) - Crop: Rose
Data fetched for point (12.7360151, 77.7601675): 31 records
Processing point (12.7360286, 77.7601616) - Crop: Rose
Data fetched for point (12.7360286, 77.7601616): 31 records
Processing point (12.7360465, 77.7601501) - Crop: Rose
Data fetched for point (12.7360465, 77.7601501): 31 records
Processing point (12.

Data fetched for point (12.7589372, 77.7506181): 31 records
Processing point (12.8030071, 77.7994564) - Crop: Ragi
Data fetched for point (12.8030071, 77.7994564): 31 records
Processing point (12.7983136, 77.8059353) - Crop: Ragi
Data fetched for point (12.7983136, 77.8059353): 31 records
Processing point (12.7605946, 77.7823886) - Crop: Rose
Data fetched for point (12.7605946, 77.7823886): 31 records
Processing point (12.7553167, 77.7918018) - Crop: Ragi
Data fetched for point (12.7553167, 77.7918018): 31 records
Processing point (12.7553159, 77.791802) - Crop: Ragi
Data fetched for point (12.7553159, 77.791802): 31 records
Processing point (12.7743625, 77.7487594) - Crop: Ragi
Data fetched for point (12.7743625, 77.7487594): 31 records
Processing point (12.7743599, 77.7487557) - Crop: Ragi
Data fetched for point (12.7743599, 77.7487557): 31 records
Processing point (12.7743749, 77.7487443) - Crop: Ragi
Data fetched for point (12.7743749, 77.7487443): 31 records
Processing point (12.7

Data fetched for point (12.7425462, 77.7641509): 31 records
Processing point (12.7425513, 77.7641539) - Crop: Rose
Data fetched for point (12.7425513, 77.7641539): 31 records
Processing point (12.7442792, 77.747543) - Crop: Rose
Data fetched for point (12.7442792, 77.747543): 31 records
Processing point (12.7442721, 77.7475459) - Crop: Rose
Data fetched for point (12.7442721, 77.7475459): 31 records
Processing point (12.7425487, 77.7641465) - Crop: Rose
Data fetched for point (12.7425487, 77.7641465): 31 records
Processing point (12.7425499, 77.7641456) - Crop: Rose
Data fetched for point (12.7425499, 77.7641456): 31 records
Processing point (12.7549569, 77.7846243) - Crop: Avare
Data fetched for point (12.7549569, 77.7846243): 31 records
Processing point (12.7549568, 77.7846243) - Crop: Avare
Data fetched for point (12.7549568, 77.7846243): 31 records
Processing point (12.8055202, 77.7720956) - Crop: Jowar
Data fetched for point (12.8055202, 77.7720956): 31 records
Processing point (1

Data fetched for point (12.7544543, 77.7453123): 31 records
Processing point (12.7544296, 77.7453244) - Crop: Rose
Data fetched for point (12.7544296, 77.7453244): 31 records
Processing point (12.7544288, 77.7453244) - Crop: Rose
Data fetched for point (12.7544288, 77.7453244): 31 records
Processing point (12.7482851, 77.7594813) - Crop: Eucalyptus
Data fetched for point (12.7482851, 77.7594813): 31 records
Processing point (12.7482857, 77.7594792) - Crop: Eucalyptus
Data fetched for point (12.7482857, 77.7594792): 31 records
Processing point (12.7442567, 77.747329) - Crop: Rose
Data fetched for point (12.7442567, 77.747329): 31 records
Processing point (12.7442633, 77.7473397) - Crop: Rose
Data fetched for point (12.7442633, 77.7473397): 31 records
Processing point (12.76572, 77.7633767) - Crop: Ragi
Data fetched for point (12.76572, 77.7633767): 31 records
Processing point (12.765861, 77.7634248) - Crop: Ragi
Data fetched for point (12.765861, 77.7634248): 31 records
Processing point

...

Data fetched for point (12.7275969, 77.6559863): 31 records
Processing point (12.727633, 77.6560706) - Crop: Eucalyptus
Data fetched for point (12.727633, 77.6560706): 31 records
Processing point (12.7194517, 77.662315) - Crop: Eucalyptus
Data fetched for point (12.7194517, 77.662315): 31 records
Processing point (12.7272344, 77.6906813) - Crop: Jowar
Data fetched for point (12.7272344, 77.6906813): 31 records
Processing point (12.6738798, 77.7333413) - Crop: Eucalyptus
Data fetched for point (12.6738798, 77.7333413): 31 records
Processing point (12.6739301, 77.7333329) - Crop: Eucalyptus
Data fetched for point (12.6739301, 77.7333329): 31 records
Processing point (12.6739559, 77.7331496) - Crop: Eucalyptus
Data fetched for point (12.6739559, 77.7331496): 31 records
Processing point (12.7281791, 77.6880451) - Crop: Jowar
Data fetched for point (12.7281791, 77.6880451): 31 records
Processing point (12.6996063, 77.7349248) - Crop: Eucalyptus
Data fetched for point (12.6996063, 77.7349248

Data fetched for point (12.7105552, 77.6355474): 31 records
Processing point (12.710555, 77.6355793) - Crop: Ragi
Data fetched for point (12.710555, 77.6355793): 31 records
Processing point (12.7161247, 77.6482744) - Crop: Ragi
Data fetched for point (12.7161247, 77.6482744): 31 records
Processing point (12.7144226, 77.6518969) - Crop: Eucalyptus
Data fetched for point (12.7144226, 77.6518969): 31 records
Processing point (12.71442753, 77.65190067) - Crop: Eucalyptus
Data fetched for point (12.71442753, 77.65190067): 31 records
Processing point (12.6725257, 77.6902355) - Crop: Ragi
Data fetched for point (12.6725257, 77.6902355): 31 records
Processing point (12.671249, 77.6776625) - Crop: Eucalyptus
Data fetched for point (12.671249, 77.6776625): 31 records
Processing point (12.6712529, 77.6776665) - Crop: Eucalyptus
Data fetched for point (12.6712529, 77.6776665): 31 records
Processing point (12.6920647, 77.6435765) - Crop: Avare
Data fetched for point (12.6920647, 77.6435765): 31 rec

Data fetched for point (12.7177116, 77.6844373): 31 records
Processing point (12.7177278, 77.6844317) - Crop: Jowar
Data fetched for point (12.7177278, 77.6844317): 31 records
Processing point (12.6779567, 77.711745) - Crop: Ragi
Data fetched for point (12.6779567, 77.711745): 31 records
Processing point (12.6779575, 77.7117607) - Crop: Ragi
Data fetched for point (12.6779575, 77.7117607): 31 records
Processing point (12.7355279, 77.6490593) - Crop: Eucalyptus
Data fetched for point (12.7355279, 77.6490593): 31 records
Processing point (12.7355226, 77.6490185) - Crop: Eucalyptus
Data fetched for point (12.7355226, 77.6490185): 31 records
Processing point (12.7351021, 77.649056) - Crop: Ragi
Data fetched for point (12.7351021, 77.649056): 31 records
Processing point (12.7351216, 77.6490523) - Crop: Ragi
Data fetched for point (12.7351216, 77.6490523): 31 records
Processing point (12.7349556, 77.6487432) - Crop: Ragi
Data fetched for point (12.7349556, 77.6487432): 31 records
Processing 

Data fetched for point (12.6699179, 77.6912097): 31 records
Processing point (12.7199753, 77.747733) - Crop: Ragi
Data fetched for point (12.7199753, 77.747733): 31 records
Processing point (12.7203971, 77.6494707) - Crop: Ragi
Data fetched for point (12.7203971, 77.6494707): 31 records
Processing point (12.7203955, 77.6494478) - Crop: Ragi
Data fetched for point (12.7203955, 77.6494478): 31 records
Processing point (12.7349167, 77.6697267) - Crop: Ragi
Data fetched for point (12.7349167, 77.6697267): 31 records
Processing point (12.6629907, 77.6901918) - Crop: Eucalyptus
Data fetched for point (12.6629907, 77.6901918): 31 records
Processing point (12.6629897, 77.6901879) - Crop: Eucalyptus
Data fetched for point (12.6629897, 77.6901879): 31 records
Processing point (12.7197852, 77.6578617) - Crop: Ragi
Data fetched for point (12.7197852, 77.6578617): 31 records
Processing point (12.7197872, 77.6578682) - Crop: Ragi
Data fetched for point (12.7197872, 77.6578682): 31 records
Processing

Data fetched for point (12.707955, 77.6723957): 31 records
Processing point (12.6700611, 77.6951864) - Crop: Eucalyptus
Data fetched for point (12.6700611, 77.6951864): 31 records
Processing point (12.6700604, 77.6951875) - Crop: Eucalyptus
Data fetched for point (12.6700604, 77.6951875): 31 records
Processing point (12.6881368, 77.687431) - Crop: Maize
Data fetched for point (12.6881368, 77.687431): 31 records
Processing point (12.7198336, 77.6578884) - Crop: Ragi
Data fetched for point (12.7198336, 77.6578884): 31 records
Processing point (12.7198356, 77.6578891) - Crop: Ragi
Data fetched for point (12.7198356, 77.6578891): 31 records
Processing point (12.7185212, 77.6390331) - Crop: Eucalyptus
Data fetched for point (12.7185212, 77.6390331): 31 records
Processing point (12.6709226, 77.6993768) - Crop: Eucalyptus
Data fetched for point (12.6709226, 77.6993768): 31 records
Processing point (12.6709194, 77.6993763) - Crop: Eucalyptus
Data fetched for point (12.6709194, 77.6993763): 31 